In [251]:
import numpy as np
import pylab as plt
#import os
#os.environ["KMP_DUPLICATE_LIB_OK"]="TRUE"
import networkx as nx
import random as rand
import tensorflow as tf
from tensorflow import keras
from collections import deque


# MDP for Continuous Space state

The framework still the same in the case of continuous space **state**. We can use the **MDP** formalism and the Bellman theory. The only part which change is that the transition probability:

$$
P(\mathbf{s}^{'}\mid \mathbf{a},\mathbf{s})
$$

is given by a probability density such that $\int_{s}P(\mathbf{s}^{'}\mid \mathbf{a},\mathbf{s})=1$. In this case we obtain new **Bellman optimality equation** given by:

$$
 V^*(\mathbf{s})  = \operatorname{max}_{\mathbf{a}} \left( R(\mathbf{s},\mathbf{a})+ \gamma \int_{s}P(\mathbf{s}^{'} | \mathbf{s},\mathbf{a}) V^*(\mathbf{s}^{'}) d\mathbf{s}^{'}\right)
$$

and

$$
 Q^*(\mathbf{s},\mathbf{a})  = \left( R(\mathbf{s},\mathbf{a})+ \gamma \int_{s}P(\mathbf{s}^{'} | \mathbf{s},\mathbf{a})  \operatorname{max}_{\mathbf{a}^{'}}Q^*(\mathbf{s}^{'},\mathbf{a}^{'}) d\mathbf{s}^{'}\right)
$$

which is equivalent to 

$$
 Q^*(\mathbf{s},\mathbf{a})  = \left( R(\mathbf{s},\mathbf{a})+ \gamma \int_{s}P(\mathbf{s}^{'} | \mathbf{s},\mathbf{a}) V^*(\mathbf{s}^{'}) d\mathbf{s}^{'}\right)
$$

# Deep Q learning

## Introduction

The principle of the Deep Q-learning is an extansion of the previous algorithm to the **Continuous state space**. In the case the $Q$ fonction is non matrix but a **function** taking $\mathbf{s}$ as input and given $\mid A \mid$ value as output.

To construct a function like that we must parametrized model to approximate the theoretical function. We can use linear or polynomial approximation for $Q(\mathbf{s},\mathbf{a})$ (which is the componant of **Q function** for the action $\mathbf{a}$).


However the current strategy is to use artifical neural network ANN to appromximate these function.
We note $Q_{\theta}(\mathbf{s},.)$ the ANN for the Q-function. We we use $Q_{\theta}(\mathbf{s},\mathbf{a})$ we speak of the output associated to the action $\mathbf{a}$.

https://lilianweng.github.io/lil-log/2018/02/19/a-long-peek-into-reinforcement-learning.html#deep-q-network


Before to introduce the Deep-Q learning **algorithm** we will propose some remark about on/off policy algorithms.

We recall: 

 - **on policy**: the policy evaluated (target policy) is the same that the policy use for exploration (behavior policy)
 - **off policy**: the policy evaluated (target policy) is not same that the policy use for exploration (behavior policy)
 
For a given policy $\pi$ an on policy algorithm evaluate $Q^{\pi}$ and a off an on policy algorithm evaluate $Q^{*}$.
The off-policy case have the advantage to guarantees that the estimate of $Q^{*}$ will keep getting more accurate even if the policy being followed changes. Indeed following $\pi_1$ will yield $Q^{*}$, following $\pi_2$ will yield $Q^*$ and randomly choosing between $\pi_1$ and $\pi_2$ for each step will still yield $Q^*$.

In the on-policy case, however, following $\pi_1$ will yield $Q_{\pi_1}$, following $\pi_2$ will yield $\pi_2$ and randomly choosing between the two policies at each step could be not good results.

## Classical Deep-Q learning

At convergence of a **Q-learning algorithm** we have:

$$
\mathbf{r}_{t+1} + \gamma \operatorname{max}_{\mathbf{a}}Q(\mathbf{s}_{t+1},\mathbf{a})-Q(\mathbf{s}_t,\mathbf{a}_t) \approx 0 
$$

which is equivalent to

$$
Q(\mathbf{s}_t,\mathbf{a}_t) \approx \mathbf{r}_{t+1} + \gamma \operatorname{max}_{\mathbf{a}}Q(\mathbf{s}_{t+1},\mathbf{a})
$$

This small computation show that the reference value for the $Q$ function is giben by $\mathbf{r}_{t+1} + \gamma \operatorname{max}_{\mathbf{a}}Q(\mathbf{s}_{t+1},\mathbf{a})$. This reference value can be used as **reference output** in the ANN training. We obtain the following **Local Loss function**:

$$
\mathcal{L}(\theta) =  \mid \mathbf{y}_{t} - Q_{\theta}(\mathbf{s}_{t},\mathbf{a}_t)\mid^2
$$

with $\mathbf{y}_t = \mathbf{r}_{t+1} + \gamma \operatorname{max}_{\mathbf{a}}Q(\mathbf{s}_{t+1},\mathbf{a})$.

However the algorithm cannot be just the classical one with the **ANN** update. Indeed It is known that for the training of the ANN is easier if we use random batch of the data.

Tipically some consecutives **states** can be very close and consequently the batch for the learning will be not representative and the training will be not accurate.

The idea called **experience replay** consist to store some transition $(\mathbf{s}_t,\mathbf{a}_t,\mathbf{r}_t,\mathbf{s}_{t+1})$ and update the ANN with **random batch transition**. 

A second key ingrediant is the **Periodically Updated Target**. The idea is to use two differents **Q-functions**, one for the evaluation of the action and another for the choice of action. This separation is also a point proposed previously in the double Q learning (but it is not an extansion). For that we not update the parameter $\theta$ all the time for the **evaulation Q-function**.

The method is an **off policy** method.

### Neural network

In this case, we will use an Neural-Network with **regression** property. The basic one is an **Multi-perceptron** Neural Network with:
- some hiiden layer,
- relu activation functions,
- a linear action function is the last layer,
- $\mathbf{x}$ as input of the ANN,
- the number of action as size of output.

**Algorithm (Deep-Q Learning with experience replay)**:
- Initialize replay memory $D$ (dequeu) with a capacity $N$,
- Initialize $Q_{\theta_1}$ randomly,
- Initialize target $\hat{Q}_{\theta_2}$ randomly with $\theta_1=\theta_2$,
- for all the episodes 1 to $T$:
 - choose a initial state $\mathbf{s}_0$
 - such that $\mathbf{s}_t$ is terminal:
     - update $\pi(\mathbf{a}_t \mid \mathbf{s}_t)$ with $Q_{\theta_1}$ for all states.
     - choose an action $\mathbf{a}_t$ using exploration policy $\pi(\mathbf{a}_t \mid \mathbf{s}_t)$
     - compute $\mathbf{r}_{t+1}$ and $\mathbf{s}_{t+1}$ using $\mathbf{a}_t$
     - store in $D$ the transition $(\phi(\mathbf{s}_t),\mathbf{a}_t,\mathbf{r}_{t+1},\phi(\mathbf{s}_{t+1}))$ with $\phi$ a preprocessing
 - construct output vector using the transition in $D$ with
     
     $$
     \mathbf{y}_j = \left\{\begin{array}{l} \mathbf{r}_{j+1} \mbox{ if $\mathbf{s}_j$ is terminal}, \forall j\in \left\{1,M\right\} \\
     \mathbf{r}_{j+1} + \gamma \operatorname{max}_{\mathbf{a}}\hat{Q}_{\theta_2}(\phi(\mathbf{s}_{j+1}),\mathbf{a}) \mbox{ else }, \forall j\in \left\{1,M\right\}
     \end{array}\right. 
     $$
   
 - sample random minibatch (size $M$) of transition choosen in $D$,
 - perform a descend gradient for the ANN resptec to $\theta_1$ with the loss:
      
  $$
  \mid \mathbf{y}_j - Q_{\theta_1}(\phi(\mathbf{s}_{j}),\mathbf{a}_j) \mid^2
  $$
     
 - every C step: $\hat{Q}_{\theta_2}=Q_{\theta_1}$
- $\pi_f(\mathbf{s}_t)=\operatorname{argmax}_{\mathbf{a}}Q(\mathbf{s}_t,\mathbf{a})$

The experience replay is fully compatible with the **off-policy** method. Indeed **the replay buffer** is an amalgamation of experiences gathered by the agent following different policies $\pi_1,..,\pi_n$ at different times.

Since the **off policy** algorithms compute $Q^{*}$ it is not a problem to use this experience replay. For the **On policy** algorithms the policy evaluate is the policy use for exploration. 

If we update our policy based on experience replay, we are actually evaluating actions from a policy that is no longer the current one, since it evolved in time, thus making it no longer on-policy. Consequently the experience replay seems not compatible with the **on policy** method.

We will see in the future that the **on policy** methods use full trajectories to learn contrary to the experience replay which mix the transition.

The experience replay which sample collection follows a behavior policy different from the target policy, bringing better exploration.

The **algorithm** use many parameters:
- $N$ (size of memory), $M$ (size of batch), $T$ number of episode,
- $\epsilon$ for the $\epsilon$-greedy case and $\lambda$ the decay parameter
- The ANN parameters,
- the optimization (ADAM for example) parameters.

## Double Deep-Q learning


The Double Deep-Q learning is the extension of the Q learning with the Deep Learning context.
In the previous algorithm we always have two $Q$-functions if $C$ different to one.
However
- the estmimator max ( in the computationof $\mathbf{y}$) is always used,
- the two $Q$-functions are the same every $C$ steps.

The Double Deep-Q learning is a similar algorithm but use the second $Q$ function **to avoid the max estimator**. In this algorithm it is also proposed to use an average update for the target $Q$-functions.

https://arxiv.org/abs/1509.06461

https://towardsdatascience.com/double-deep-q-networks-905dd8325412

**Algorithm (Double Deep-Q Learning with experience replay)**:
- Initialize replay memory $D$ (dequeu) with a capacity $N$,
- Initialize $Q_{\theta_1}$ randomly,
- Initialize target $\hat{Q}_{\theta_2}$ randomly with $\theta_1=\theta_2$,
- for all the episodes 1 to $T$:
 - choose a initial state $\mathbf{s}_0$
 - such that $\mathbf{s}_t$ is terminal:
     - update $\pi(\mathbf{a}_t \mid \mathbf{s}_t)$ with $Q_{\theta_1}$ for all states.
     - choose an action $\mathbf{a}_t$ using exploration policy $\pi(\mathbf{a}_t \mid \mathbf{s}_t)$
     - compute $\mathbf{r}_{t+1}$ and $\mathbf{s}_{t+1}$ using $\mathbf{a}_t$
     - store in $D$ the transition $(\phi(\mathbf{s}_t),\mathbf{a}_t,\mathbf{r}_{t+1},\phi(\mathbf{s}_{t+1}))$ with $\phi$ a preprocessing
 - construct output vector using the transition in $D$ with
     
      $$
     \mathbf{y}_j = \left\{\begin{array}{l} \mathbf{r}_j \mbox{ if $\mathbf{s}_j$ is terminal}, \forall j\in \left\{1,M\right\} \\
     \mathbf{r}_{j} + \gamma Q_{\theta_1}(\phi(\mathbf{s}_{j+1}),\mathbf{a}^*) \mbox{ else }, \forall j\in \left\{1,M\right\}
     \end{array}\right. 
     $$
 
     - with $\mathbf{a}^{*}= \operatorname{argmax}_{\mathbf{a}} \hat{Q}_{\theta_2}(\phi(\mathbf{s}_{j+1}),\mathbf{a})$
   
 - sample random minibatch (size $M$) of transition choosen in $D$,
 - perform a descend gradient for the ANN resptec to $\theta_1$ with the loss:
      
  $$
  \mid \mathbf{y}_j - Q_{\theta_1}(\phi(\mathbf{s}_{j}),\mathbf{a}_j) \mid^2
  $$
  
 - update the parameters $\theta_2$ parameters with $\theta_2 := \tau \theta_1 + (1-\tau) \theta_2$ 

- $\pi_f(\mathbf{s}_t)=\operatorname{argmax}_{\mathbf{a}}Q(\mathbf{s}_t,\mathbf{a})$

